In [1]:
import spacy
import pandas as pd
import glob
import tqdm

In [2]:
files = glob.glob("Database/*/CONLL/*.xlsx")
print(len(files))

17


In [26]:
def group_acts(df):
    if "ACT" in df.columns:
        group_col = "ACT"
    elif "Original_Act_ID" in df.columns:
        group_col = "Original_Act_ID"
    else:
        "unknown"

    if "LANG" in df.columns:
        df = df[df["LANG"] == "LAT"]

    df['Word_x'] = df['Word_x'].astype(str).str.strip()
    
    # Combine words into sentences, assumed by unique 'Line_ID'
    grouped_data = df.groupby(group_col)

    return grouped_data

def create_spacy_doc(df, nlp):
    grouped_df = group_acts(df)
    docs = []
    
    for key, group in grouped_df:
        tokens = []
        spaces = []
        entities = []
        current_entity = None

        # Iterate over the rows in the group
        for i, row in enumerate(group.itertuples()):
            word = row.Word_x
            length_word = len(word)
            # Check if there is a next word and whether it should be followed by a space
            space_after = not (i < len(group) - 1 and group.iloc[i + 1].Word_x in [',', '.', ';', ':'])
            tokens.append(word)
            spaces.append(space_after)

            # Handle entity recognition
            if row.PERS_x != 'O':
                entity_type = 'PERSON'
            elif row.LOC_x != 'O':
                entity_type = 'LOC'
            else:
                entity_type = None

            if current_entity is None and entity_type is not None:
                # Start new entity
                current_entity = [i, i, entity_type]
            elif current_entity is not None:
                if entity_type == current_entity[2]:
                    # Extend current entity
                    current_entity[1] = i
                else:
                    # Finish current entity and add to entities list
                    entities.append(current_entity)
                    current_entity = [i, i, entity_type] if entity_type else None

        # Check if an entity is still open at the end of the group
        if current_entity is not None:
            entities.append(current_entity)

        # Create a spacy Doc object
        doc = spacy.tokens.Doc(nlp.vocab, words=tokens, spaces=spaces)
        # Get the sentencizer component from the pipeline
        sentencizer = nlp.get_pipe("sentencizer")

        # Apply the sentencizer to the Doc
        sentencizer(doc)
        # Create Span objects for the entities
        spans = [doc.char_span(doc[ent[0]].idx, doc[ent[1]].idx + len(doc[ent[1]].text), label=ent[2])
                 for ent in entities if doc.char_span(doc[ent[0]].idx, doc[ent[1]].idx + len(doc[ent[1]].text), label=ent[2])]
        doc.spans["sc"] = spans
        

        docs.append(doc)

    return docs


In [27]:

docs = []
nlp = spacy.blank("en")
nlp.add_pipe("sentencizer")

for file in tqdm.tqdm(files):
    df = pd.read_excel(file)
    docs = docs+create_spacy_doc(df, nlp)

  0%|          | 0/17 [00:00<?, ?it/s]/var/folders/4f/ddlj81h90_n0_h5wwvjbd2b40000gn/T/ipykernel_8164/298127518.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Word_x'] = df['Word_x'].astype(str).str.strip()
  6%|▌         | 1/17 [00:01<00:23,  1.45s/it]/var/folders/4f/ddlj81h90_n0_h5wwvjbd2b40000gn/T/ipykernel_8164/298127518.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Word_x'] = df['Word_x'].astype(str).str.strip()
 12%|█▏        | 2/17 [00:03<00:26,  1.77s/it]/var/folders/4f/ddlj81h9

In [40]:
hf_docs = []
hf_docs_sents = []
for doc in docs:
    tokenized_text = [token.text for token in doc]
    spans = [{"text": span.text, "label": span.label_, "start": span.start, "end": span.end} for span in doc.spans["sc"]]
    hf_docs.append({"tokenized_text": tokenized_text, "spans": spans})
    for sent in doc.sents:
        sent_doc = sent.as_doc()  # Create a new Doc from the sentence
        
        # Create a list of spans that are within the boundaries of this sentence
        sent_spans = [
            {"start": span.start - sent.start, "end": span.end - sent.start, "label": span.label_, "text": span.text}
            for span in doc.spans["sc"] if span.start >= sent.start and span.end <= sent.end
        ]
        
        # Check if there are entities in the sentence, if yes, add to hf_docs_sents
        if sent_spans:
            hf_docs_sents.append({
                "tokenized_text": [token.text for token in sent],
                "spans": sent_spans,
                "ms": {}  # Assuming 'ms' should be some metadata, define or update accordingly
            })
hf_docs[0]

{'tokenized_text': ['In',
  'nomine',
  'Domini',
  ',',
  'amen',
  '.',
  'Ego',
  'Mauricius',
  ',',
  'Dei',
  'gracia',
  'Parisiensis',
  'episcopus',
  ',',
  'universitati',
  'presencium',
  'ac',
  'futurorum',
  'hujus',
  'pagine',
  'attestatione',
  'notificare',
  'curamus',
  'quod',
  'dominus',
  'Guido',
  'de',
  'Levies',
  ',',
  'pia',
  'et',
  'honesta',
  'consideratione',
  'ductus',
  ',',
  'ad',
  'edificandam',
  'quandam',
  'novellam',
  'plantationem',
  ',',
  'amore',
  'Dei',
  'et',
  'remedio',
  'anime',
  'sue',
  'et',
  'animarum',
  'parentum',
  'predecessorum',
  'suorum',
  ',',
  'fratribus',
  'ibi',
  'Deo',
  'servituris',
  'in',
  'perpetuam',
  'elemosinam',
  'donavit',
  'unam',
  'carrucam',
  'de',
  'terra',
  'quam',
  'emit',
  'des',
  'Fers',
  'Dasnois',
  ',',
  'et',
  'de',
  'decima',
  'duas',
  'partes',
  'quas',
  'ab',
  'hiisdem',
  'emit',
  ',',
  'et',
  'unam',
  'partem',
  'nemoris',
  'quantum',
  'semita

In [33]:
len(hf_docs_sents)

15141

In [34]:
import srsly

In [35]:
srsly.write_jsonl("home-alcar-ner.jsonl", hf_docs)

In [39]:
srsly.write_jsonl("home-alcar-ner-sents.jsonl", hf_docs_sents)